# Wind Speed Estimation and Conversion
#### M. Bakhshandeh; Florida Institute of Technology
#### Jean-Paul Pinelli; Florida Institute of Technology
#### Date: 01/10/2025

-------------
## Summary
This Jupyter notebook interpolates wind speed data from any given hurricane to any location in Florida.The input data can be provided on any arbitrary grid. It can be provided for different types of exposure and average time intervals at different heights. It accepts input data on any grid format and handles different exposure types (like marine conditions, open terrain, or urban terrain) and time averages (including 3-second gusts, 1-minute sustained winds, and 10-minute averages). It performs three key functions: (1) linear interpolation from source grid points to target locations, (2) conversion between exposure types and time intervals using modular, and (3) conversion form one height to another.

The Jupyter notebook first interpolates wind speeds to exact property coordinates using linear interpolation, then applies terrain adjustments accounting for urban drag, coastal, and surface roughness effects derived from GeoTIFF data to get actual terrain wind speeds at the policy. For example, Applied Research Associates (ARA) (under contract with the National Institute of Standardsand Technology or NIST) provides both 10 m open-terrain 3-second gusts and 1-minute sustained winds field data on a grid, for all hurricanes from 2017 onward. These data are published in DesignSafe. For any hurricane processed by ARA (e.g. hurricane Michael) the notebook interpolates the ARA 3-secondgusts or 1-minute sustained winds for any given location, then adjusts these values based on terrain roughness (e.g. urban, coastal, or forested), to get actual terrain wind speeds at that location. Outputsinclude both interactive visualizations maps and standardized CSV files.

This notebook consists of three main operations:
1. Configuration & Input Detection
Reads and validates all settings from config1.txt (file paths, exposure, time‐interval, heights, rasters, outputs) and infers which wind column to use.

2. Interpolation of wind speeds to property locations
Uses SciPy’s griddata to linearly interpolate the configured wind‐speed column from the source grid onto each property’s Lon/Lat.

3. Conversion of the estimated wind speeds to actual-terrain gusts
Reads GeoTIFF rasters and gust-factor tables, performs terrain and urban adjustments, and computes the final 10 m 3s actual-terrain gusts (Applies marine-basis conversion if needed).

------------- 
## Methodology  
The Jupyter Notebook converts hurricane wind field data into property-level wind speed estimates. The methodology addresses the user’s need for location-specific wind estimation.
The model begins by preparing and validating input data, accepting wind field information in any grid format while ensuring coordinate accuracy and proper unit conversion. The initial validation step guarantees that all subsequent calculations begin with clean, reliable data.
The core of the analysis lies in the spatial interpolation stage, where the notebook calculates wind speed estimates at any specified location. The input data and the corresponding interpolated data can be for different time averages (e.g. 3-second gust or 1-minute sustained wind).
The model then applies validated terrain adjustments. These modifications account for real-world environmental factors including urban drag effects, coastal wind enhancements, and surface roughness variations derived from high-resolution GeoTIFF data. 
Each adjustment follows established meteorological principles. This data was provided by Dr. Steven Cocke (Florida State University) through a dedicated Jupyter notebook, which is incorporated in this model. The imported dataset—preserving its original formulas, databases, and methodology—accounts for:
•	Urban Drag: Reduces wind speeds by 15% in cities (buildings create friction)
•	Coastal Effects: Boosts winds near shorelines (+10-15%)
•	Surface Roughness: Adjusts for terrain exposure like forests, fields, and water (using roughness coefficients z₀ values from GeoTIFF files)
The final stage is a map visualization.
The methodology comprises the following key stages.
  
### Data Preparation & Configuration

The methodology begins with data preparation to ensure correct inputs. The model requires two primary datasets: wind field data in CSV format from any given location with different exposure types (marine, open terrain, urban) and time‐averages (3-second gusts, 1-minute sustained, 10-minute averages); and property location data with policy IDs and geographic coordinates (longitude, latitude).  For physical calculations in subsequent stages, wind speed units are converted from miles per hour (mph) to meters per second (m/s) using a standard conversion factor of 0.44704. This unit standardization ensures compatibility with terrain adjustment formulas and wind profile equations.

- **Wind Field CSV**  
  - Arbitrary grid; any height or exposure  
  - Columns: `Longitude`, `Latitude`, plus one or more wind‐speed fields  
  - `config1.txt` must supply:  
    - `wind_data`, `wind_speed_columns`  
    - `input_exposure_type` (open_terrain|marine|urban)  
    - `input_time_interval` (gust_3s|sustain_1min|avg_10min)  
    - `reference_height`, `target_height`  
- **Property Locations CSV**  
  - Required: `ID`, `Lon`, `Lat`  
- **Terrain Rasters**  
  - `rough_2022.tif` → surface roughness z₀  
  - `distance_2022.tif` → distance to coastline (km)  
- **Gust-Factor Binaries**  
  - `gfac_3sec.dat`, `gfac2_3sec.dat`, `gfacm.dat`, `gfaco.dat`  

**Preprocessing:**  
- Coordinate validation (−180→180°, −90→90°)  
- Unit conversion (mph/knots → m/s)  
- Data integrity checks (NaNs, ranges)  

### Wind Interpolation

The wind speed interpolation process employs a deterministic linear interpolation approach using scipy.interpolate.griddata with the linear method. This algorithm estimates both open-terrain 3-second gust wind speeds (mph) and 1-minute sustained wind speeds (mph) at each property location by analyzing the surrounding wind field data points. The mathematical foundation uses inverse distance weighting, where the interpolated value V_interp(x,y) is calculated as the weighted sum of nearby wind speeds (Formula 1). The implementation handles edge cases systematically; for coordinates falling outside the wind field grid boundaries, it applies nearest-neighbor extrapolation to provide reasonable estimates, while explicitly maintaining null values (NaN) for locations where reliable interpolation cannot be performed. The results are output in a structured CSV format containing property coordinates alongside their corresponding interpolated wind values, ensuring the data remains organized for subsequent terrain adjustment processing.

The wind speed at any given location (x,y) is estimated by calculating a weighted average of observed wind speeds from nearby measurement points or stations. This process accounts for spatial variation by giving more influence to closer stations.

- **Formula (1):**  
  $$
  V_{\rm interp}(x,y)
  = \sum_i w_i\,V_i,
  \quad
  w_i = \frac{1/d_i}{\sum_j 1/d_j},
  \;d_i=\sqrt{(x-x_i)^2+(y-y_i)^2}.
  $$  
- **Outputs:** New columns `WindSpeed_3_gust`, `WindSpeed_1_sust`, etc.

N.B. When the target location lies outside the coverage area of the wind field grid (beyond the nearest stations), the interpolation uses the nearest-neighbor method, i.e., the wind speed from the closest station is assigned directly.
If, after interpolation, the wind speed value is missing (NaN), the property or location is skipped or excluded from further analysis to avoid errors or bias.

---

### Wind Speeds Conversion  
This stage transforms the interpolated “reference” wind (10 m, marine-10 min basis) into actual-terrain 3s gusts by adjusting it according to local terrain characteristics, resulting in an actual, site-specific wind speed estimate. The process involves several phases:

#### Terrain-Specific Wind Adjustment

The model uses the rough_2022.tif GeoTIFF raster, which is provided by Dr. Steven Cocke (Florida State University) through a dedicated Jupyter notebook, which maps terrain roughness lengths (z₀) across the study area. Terrain is classified into four main categories, each with a characteristic roughness range: 
o	Water surfaces: z₀ = 0.0002–0.002 m
o	Open terrain: z₀ = 0.002–0.03 m
o	Forested areas: z₀ = 0.03–0.4 m
o	Urban environments: z₀ = 0.4–1.0 m
The roughness length z₀ influences how wind speed varies with height above the ground.

#### Wind Profile Adjustment Using Logarithmic Scaling

The wind speed at height z (V_z) is calculated from the reference wind speed at 10 m height over open terrain (V_10) by applying the logarithmic wind profile formula (Formula 2):

**Formula (2)**:  
   $$
   V_z = V_{10}\,\frac{\ln(z/z_0)}{\ln(10/z_0)}
   $$
 V_10: Wind speed at 10m height (open terrain).
V_z: Wind speed at height z.

#### Coastal Proximity Effects 

Coastal zones experience different wind dynamics due to the transition from water to land surfaces. The model uses the distance_2022.tif raster, which is provided by Dr. Steven Cocke (Florida State University) through a dedicated Jupyter notebook, to compute the distance of each location from the coastline. Within 50 km of the shore, specialized gust factor tables (gfac2_3sec.dat) are applied to adjust wind gusts, capturing the marine-to-terrain transition effects on wind behavior.

**Coastal Transition**:  
   - ≤ 50 km: use `gfac2_3sec.dat`  
   - > 50 km: use `gfac_3sec.dat`  

**Urban Drag**:  
   - If z₀ > 0.4 m, reduce by 15 %  

**Time-Basis Conversion**:  
   - 1 min → 10 min via `gfacm.dat` / `gfaco.dat`  
   - Gust ↔ 10 min invert via `gfac_3sec.dat`  

---

### Mapping & Visualization  
This report presents two complementary approaches to visualize actual terrain-adjusted wind speed data, each with distinct strengths and suited for different purposes:

#### I.	Static Geospatial Map with Matplotlib

This method generates a static map where data points are displayed as scatter points colored according to the actual 10 m height, 3-second gust wind speed (ActualT_3sg), utilizing a reversed Inferno colormap to enhance contrast. The Florida state boundaries are approximated by limiting the map extents, and a high-resolution satellite basemap from Esri World Imagery is incorporated to provide geographic context. The map features a vertical colorbar, a title, and a clean layout with axes hidden for clarity.

#### II.	Interactive Web Map with Folium

This method creates an interactive web map that can be embedded in Jupyter notebooks or saved as a standalone HTML file. The map is centered on the mean latitude and longitude of the filtered dataset, adapting dynamically to the geographic extent of the data—Florida in this case, but applicable to other regions or states. Wind speed data points are represented as color-coded circle markers using a sequential YlOrRd colormap scaled to the range of wind speeds. Each marker features a clickable pop-up providing detailed, location-specific information, including geographic coordinates, ActualT_3sg, z0_raster, and dist_raster, aiding in the interpretation of local wind conditions. Additional interactive features, such as a color legend, minimap overview, and layer control widgets, enhance usability. The map can be saved as an HTML file for viewing in any web browser or displayed directly within a Jupyter Notebook.

**Exports:**  
- `interpolated.csv`
- `wind speeds conversion.csv`
- `HTML file`
------
#### Data Sources and Confidentiality

The Jupyter notebook also requires input files containing the latitude and longitude of the analyzed properties. These data can be obtained either from insurance claim records or from publicly available reconnaissance datasets (such as those hosted on the DesignSafe Reconnaissance Portal).

For insurance-related data, confidentiality restrictions may apply. Users are responsible for ensuring that any proprietary or sensitive information is handled in compliance with data privacy agreements and institutional policies. The dataset used in this notebook does not contain any company identifiers or personally identifiable information, ensuring confidentiality is maintained.

##### Acknowledgements
This research was supported by the National Science Foundation (NSF) through the following awards: DesignSafe Cyberinfrastructure, Award No. 2022469. The opinions, conclusions, and results presented in this document are solely those of the authors and do not necessarily represent the views of the NSF.

The authors would like to thank Dr. Steve Cocke of Florida State University for his valuable assistance in developing the Jupyter notebook and for providing the surface roughness GeoTIFF dataset used to characterize terrain exposure across Florida. His technical insights and data contributions were instrumental in the development of this Jupyter notebook.


### Data Preparation & Configuration 
This section initializes core data processing libraries (pandas, numpy) and interpolation tools (scipy.interpolate.griddata). 
It also defines a load_config function to parse a configuration file, extracting parameters like wind_speed_columns as a list, and loads these settings for downstream tasks.


In [6]:
from pathlib import Path
import pandas as pd

# locate config
cfg_path = Path("Configuration/config1.txt").resolve()
print("Using config:", cfg_path)
cfg_dir = cfg_path.parent

# quick parser (same logic as loader but minimal)
cfg = {}
with cfg_path.open('r', encoding='utf-8') as f:
    for raw in f:
        line = raw.strip()
        if not line or line.startswith('#'):
            continue
        if '#' in line:
            line = line.split('#',1)[0].rstrip()
        if '=' not in line:
            continue
        k, v = line.split('=',1)
        cfg[k.strip()] = v.strip()
# resolve expected path keys
path_keys = ['wind_data','property_data','terrain_raster','distance_raster',
             'intermediate_output','final_output_gust']
resolved = {}
missing = []
for k in path_keys:
    if k in cfg:
        p = Path(cfg[k])
        if not p.is_absolute():
            p = (cfg_dir / p).resolve()
        resolved[k] = p
        exists = p.exists()
        print(f"{k}: {p} -> exists: {exists}")
        if not exists:
            missing.append((k, p))
    else:
        print(f"{k} not set in config")

if missing:
    print("\nMissing files (please confirm exact folder names):")
    for k,p in missing:
        print(f" - {k}: {p}")
else:
    # if all good, attempt to read small headers
    print("\nAll configured files found — showing CSV heads (if CSVs):")
    print("Wind head:")
    print(pd.read_csv(resolved['wind_data']).head(3))
    print("\nProps head:")
    print(pd.read_csv(resolved['property_data']).head(3))


Using config: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Configuration/config1.txt
wind_data: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Wind-field Data/Michael_windgrid.csv -> exists: True
property_data: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Property Locations/WSC_Index_ lat long files _ Michael/wsc_S_Michael_Res_2018_GC_XC.csv -> exists: True
terrain_raster: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Terrain Rasters/rough_2022.tif -> exists: True
distance_raster: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Terrain Rasters/distance_2022.tif -> exists: True
intermediate_output: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Interpolation&ConversionOutput/interpolated.csv -> exists: True
final_output_gust: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Interpolation&ConversionO

### Wind Speed Interpolation
This section spatially interpolates gridded wind speed data (e.g., gust/sustained winds) onto property locations using scipy’s griddata with linear interpolation.
The function validates input columns, estimates site-specific wind speeds, appends results as new columns (e.g., WindSpeed_3_gust), and saves the enhanced dataset for damage correlation analysis.

In [2]:
# ──────────────────────────────────────────────────────────────
# Wind Speed Interpolation
# ──────────────────────────────────────────────────────────────
import pandas as pd
from scipy.interpolate import griddata
from pathlib import Path

# --- verify required inputs exist ---
for var in ['cfg', 'resolved']:
    if var not in globals():
        raise RuntimeError(f"{var} must be loaded before running interpolation.")

# Load wind and property CSVs using resolved paths
df_wind  = pd.read_csv(resolved['wind_data'])
df_props = pd.read_csv(resolved['property_data'])

# --- column mapping based on your CSV headers ---
colmap = {
    'gust_3s': 'WindSpeed (3 gust _ mph)',
    'sustain_1min': 'WindSpeed (1 sust_mph)'
    # 'avg_10min' not present in your CSV; omit or add if available
}

# ─── BUILD SUFFIX MAP ─────────────────────────────────────────
suffix_map = {
    'gust_3s':      'OT_3sg.',
    'sustain_1min': 'OT_1msust.',
    'avg_10min':    'M_10m.'
}

# ─── PREPARE COORDINATES FOR INTERPOLATION ────────────────────
known_pts  = df_wind[['Longitude', 'Latitude']].values
target_pts = df_props[['Lon', 'Lat']].values

# ─── INTERPOLATE EACH DETECTED COLUMN ────────────────────────
new_cols = []
for key, wind_col in colmap.items():
    if key not in suffix_map:
        continue
    suffix  = suffix_map[key]
    out_col = f"W_{suffix}"
    df_props[out_col] = griddata(
        points = known_pts,
        values = df_wind[wind_col].values,
        xi     = target_pts,
        method = 'linear'
    )
    new_cols.append(out_col)
    print(f" → Interpolated '{wind_col}' → '{out_col}'")

# ─── PREVIEW PROPERTIES + INTERPOLATED COLUMNS ───────────────
coord_cols = ['Lon', 'Lat']
if 'WSC_index' in df_props.columns:
    coord_cols = ['WSC_index'] + coord_cols

print("\n=== Properties & interpolated winds (first 10 rows) ===")
print(df_props[coord_cols + new_cols].head(10))

# ─── SAVE INTERMEDIATE RESULT ────────────────────────────────
out_csv = Path(resolved['intermediate_output'])
out_dir = out_csv.parent
if not out_dir.exists():
    out_dir.mkdir(parents=True, exist_ok=True)

df_props.to_csv(out_csv, index=False)
print(f"\n✅ Saved interpolated winds to: {out_csv}")


 → Interpolated 'WindSpeed (3 gust _ mph)' → 'W_OT_3sg.'
 → Interpolated 'WindSpeed (1 sust_mph)' → 'W_OT_1msust.'

=== Properties & interpolated winds (first 10 rows) ===
   WSC_index        Lon        Lat   W_OT_3sg.  W_OT_1msust.
0          0 -86.605099  30.453001   45.813242     36.139226
1          1 -84.848891  30.703424  121.591008     95.294243
2          2 -85.534012  30.423135  118.694196     93.008761
3          3 -85.606832  30.245866  127.668833    102.344736
4          4 -85.584075  30.138731  135.339145    109.474116
5          5 -85.705194  30.174159  122.728799     96.307302
6          6 -85.659498  30.197097  124.379001     97.497220
7          7 -85.610830  30.231756  126.509162     99.816393
8          8 -85.672653  30.411633  109.214704     85.516963
9          9 -85.670032  30.206817  123.259720     96.615264

✅ Saved interpolated winds to: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Interpolation&ConversionOutput/interpolated.csv


### Wind Speeds Conversion 
This section converts interpolated wind speeds to actual terrain wind speeds at the policy using raster-based roughness/distance-to-coast data and gust factor tables. 
It handles unit conversions (mph ↔ m/s ↔ knots), applies terrain exposure corrections via lookup tables, and outputs heightspecific wind profiles for damage modeling compatibility.

In [3]:
# ============================================================
# Wind Speeds Conversion
# ============================================================

!pip install rasterio
import numpy as np
import pandas as pd
import rasterio
from pathlib import Path

# ─── CONFIG LOADER ─────────────────────────────────────────────
def load_config(config_path=None):
    """
    Reads a config file of key=value pairs, ignoring comments (#).
    Automatically searches relative to this notebook if path not given.
    """
    if config_path is None:
        # Default: look for config in Configuration/config1.txt
        config_path = Path("Configuration/config1.txt")
    config_path = Path(config_path).expanduser().resolve()
    
    cfg = {}
    with open(config_path, "r") as f:
        for line in f:
            line = line.strip()
            if not line or line.startswith("#"):
                continue
            if "=" in line:
                k, v = [s.strip() for s in line.split("=", 1)]
                cfg[k] = v
    cfg["_config_dir"] = str(config_path.parent)
    return cfg

# helper to resolve relative paths
def _resolve_cfg_path(cfg, key):
    p = Path(cfg[key])
    cfg_dir = Path(cfg["_config_dir"])
    if not p.is_absolute():
        return (cfg_dir / p).resolve()
    return p

# ─── 1. LOAD CONFIG & PATHS ───────────────────────────────────
cfg = load_config()  # automatically loads Configuration/config1.txt

interp_csv   = _resolve_cfg_path(cfg, 'intermediate_output')
output_csv   = _resolve_cfg_path(cfg, 'final_output_gust')

# terrain rasters
rough_fn     = _resolve_cfg_path(cfg, 'terrain_raster')
dist_fn      = _resolve_cfg_path(cfg, 'distance_raster')

# gust-factor binaries (relative to project folder)
gfac_fn  = _resolve_cfg_path(cfg, 'gfac_file')  if 'gfac_file'  in cfg else Path("Gust-Factor Binaries/gfac_3sec.dat")
gfac2_fn = _resolve_cfg_path(cfg, 'gfac2_file') if 'gfac2_file' in cfg else Path("Gust-Factor Binaries/gfac2_3sec.dat")
gfacm_fn = _resolve_cfg_path(cfg, 'gfacm_file') if 'gfacm_file' in cfg else Path("Gust-Factor Binaries/gfacm.dat")
gfaco_fn = _resolve_cfg_path(cfg, 'gfaco_file') if 'gfaco_file' in cfg else Path("Gust-Factor Binaries/gfaco.dat")

time_int = cfg['input_time_interval']
exposure = cfg['input_exposure_type']

# ─── 2. UNIT CONVERSIONS & TABLE DIMENSIONS ───────────────────
nz, nu, nh, maxd = 100, 100, 15, 200
mph2ms, ms2mph   = 1/2.2369362921, 2.2369362921

# ─── 3. LOAD INTERPOLATED WIND DATA ───────────────────────────
df = pd.read_csv(interp_csv)

suffix_map = {
    'gust_3s':      'OT_3sg.',
    'sustain_1min': 'OT_1msust.',
    'avg_10min':    'M_10m.'
}
prop_col = f"W_{suffix_map[time_int]}"

# ─── 4. PREPARE MARINE‐10 MIN CONVERSION ───────────────────────
gfacm = np.fromfile(gfacm_fn, dtype=np.float32, count=nu) * mph2ms
gfaco = np.fromfile(gfaco_fn, dtype=np.float32, count=nu) * mph2ms

cv2ma10 = np.ones(nu)
if time_int == 'sustain_1min':
    table = gfaco if exposure=='open_terrain' else gfacm
    loops = 4 if exposure=='open_terrain' else 3
    for sp in range(nu):
        i10 = sp
        for _ in range(loops):
            c   = max(table[i10], 1.0)
            u10 = sp / c
            i10 = min(int(round(u10)), nu-1)
        cv2ma10[sp] = 1 / max(table[i10], 1.0)

# ─── 5. LOAD GUST‐FACTOR TABLES & RASTERS ─────────────────────
gfac  = (np.fromfile(gfac_fn,  dtype=np.float32, count=nh*nz*nu)
            .reshape(nh,nz,nu) * mph2ms)
gfac2 = (np.fromfile(gfac2_fn, dtype=np.float32, count=nh*nz*nu*maxd)
            .reshape(nh,nz,nu,maxd) * mph2ms)

ds_r   = rasterio.open(rough_fn); r   = ds_r.read()
ds_d   = rasterio.open(dist_fn);  dis = ds_d.read()
rows, cols = ds_r.height, ds_r.width
zoa = np.array([10**(-3 + 3*(i+1)/nz) for i in range(nz)])

# ─── 6. COMPUTE ACTUAL‐TERRAIN 3 s GUST @10 m ─────────────────
z0_list, dist_list, coastal_factor_list, gust_list = [], [], [], []

for _, R in df.iterrows():
    w_in = R.get(prop_col, np.nan)
    if not np.isfinite(w_in):
        z0_list.append(np.nan)
        dist_list.append(np.nan)
        coastal_factor_list.append(np.nan)
        gust_list.append(np.nan)
        continue

    w_ms = w_in * mph2ms
    iu   = int(round(w_ms)); iu = np.clip(iu,0,nu-1)

    if time_int == 'OT_3sg.':
        j,i = ds_r.index(R.Lon, R.Lat)
        j,i = np.clip(j,0,rows-1), np.clip(i,0,cols-1)
        iz   = np.clip(int(r[0,j,i]) - 1, 0, nz-1)
        w10  = w_ms / gfac[0,iz,iu]
        iu2  = int(round(w10))
    else:
        w10  = w_ms * cv2ma10[iu]
        iu2  = int(round(w10))

    iu2 = np.clip(iu2,0,nu-1)

    j,i = ds_r.index(R.Lon, R.Lat)
    j,i = np.clip(j,0,rows-1), np.clip(i,0,cols-1)
    iz   = np.clip(int(r[0,j,i]) - 1, 0, nz-1)
    ix   = np.clip(int(dis[0,j,i]) - 1, 0, maxd-1)

    z0_list.append(zoa[iz])
    dist_list.append(dis[0,j,i])

    gf2    = gfac2[0,iz,iu2,ix]
    gust10 = gf2 * w10 * ms2mph
    gust_list.append(gust10)
    coastal_factor_list.append(gf2)

# ─── 7. SAVE RESULTS ──────────────────────────────────────────
df['z0_raster']      = z0_list
df['dist_raster']    = dist_list
df['CoastalFactor']  = coastal_factor_list
df['ActualT_3sg']    = gust_list

df.to_csv(output_csv, index=False)
print(f"✔ Saved actual‐terrain gusts and coastal factors to: {output_csv}")


✔ Saved actual‐terrain gusts and coastal factors to: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Interpolation&ConversionOutput/Wind speeds conversion.csv


### Mapping & Visualization
This section presents two complementary approaches to visualize actual terrain-adjusted wind speed data.

In [4]:
# --- 1. Load CSV using relative path ---
from pathlib import Path
import pandas as pd
import folium
from folium.plugins import MiniMap
from branca.colormap import linear

csv_rel_path = Path("Interpolation&ConversionOutput/Wind speeds conversion.csv")
csv_path = csv_rel_path.resolve()
print("Loading CSV from:", csv_path)

df = pd.read_csv(csv_path)

# --- 2. Clean column names ---
df.columns = df.columns.str.strip().str.replace(".", "", regex=False)

# --- 3. Remove rows with missing coordinates ---
df = df.dropna(subset=["Lat", "Lon"])

# --- 4. Use the converted gust column directly ---
gust_col = "ActualT_3sg"
if gust_col not in df.columns:
    raise RuntimeError(f"Column '{gust_col}' not found in CSV.")

# --- 5. Apply wind speed threshold filter ---
wind_threshold = 0
filtered_df = df[df[gust_col] >= wind_threshold].copy()

# --- 6. Create base map centered around average location ---
map_center = [filtered_df["Lat"].mean(), filtered_df["Lon"].mean()]
m = folium.Map(location=map_center, zoom_start=6)

# --- 7. Add tile layers ---
folium.TileLayer('OpenStreetMap').add_to(m)
folium.TileLayer('CartoDB positron').add_to(m)

# --- 8. Define color scale ---
wind_min = filtered_df[gust_col].min()
wind_max = filtered_df[gust_col].max()
colormap = linear.YlOrRd_09.scale(wind_min, wind_max).to_step(n=10)
colormap.caption = "Wind Speed"

# --- 9. Add points ---
for _, row in filtered_df.iterrows():
    folium.CircleMarker(
        location=[row['Lat'], row['Lon']],
        radius=5,
        color=colormap(row[gust_col]),
        fill=True,
        fill_color=colormap(row[gust_col]),
        fill_opacity=0.8,
        popup=folium.Popup(
            html=(
                "<div style='width: 250px; padding: 5px; font-size: 10px; line-height: 1; background-color: white;'>"
                f"<b>Coordinates:</b> Lon = {row['Lon']:.5f}, Lat = {row['Lat']:.5f}<br>"
                f"<b>{gust_col}:</b> {row[gust_col]:.2f} mph<br>"
                f"<b>Surface roughness (z0):</b> {row.get('z0_raster', 0):.2f}<br>"
                f"<b>Distance to coastline:</b> {row.get('dist_raster', 0):.2f} km"
                "</div>"
            ),
            max_width=400
        )
    ).add_to(m)

# --- 10. Add legend, minimap, and controls ---
colormap.add_to(m)
MiniMap(toggle_display=True).add_to(m)
folium.LayerControl().add_to(m)

# --- 11. Save map ---
m.save("wind_map.html")
print("Map saved as 'wind_map.html'.")

# --- 12. Display inline ---
m


Loading CSV from: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Interpolation&ConversionOutput/Wind speeds conversion.csv
Map saved as 'wind_map.html'.


### Example: Interactive Wind Speed Estimation & Conversion
These functions enable manual coordinate input for two workflows:

In [5]:
# === Interactive lookup against the conversion CSV ===
import os
import numpy as np
import pandas as pd
from scipy.spatial import cKDTree
from math import radians, sin, cos, asin, sqrt
import folium
from IPython.display import display, Markdown
from pathlib import Path

# --- Resolve CSV path from config (use final_output_gust, not intermediate_output) ---
def resolve_conversion_csv(cfg):
    # prefer explicit final output file
    if 'final_output_gust' in cfg and cfg['final_output_gust']:
        p = Path(cfg['final_output_gust'])
    elif 'intermediate_output' in cfg and cfg['intermediate_output']:
        # fallback only if final_output_gust missing — but don't append filenames to file paths
        p = Path(cfg['intermediate_output'])
    else:
        # last resort: use the original hard-coded path (kept for backwards compatibility)
        p = Path("Interpolation&ConversionOutput/Wind speeds conversion.csv")
    
    # if relative, resolve relative to config dir if provided
    cfg_dir = Path(cfg.get('_config_dir', Path.cwd()))
    if not p.is_absolute():
        p = (cfg_dir / p).resolve()
    return p

CSV_PATH = resolve_conversion_csv(cfg)
print("Using conversion CSV path:", CSV_PATH)

# helpful list of nearby CSVs if the expected file is missing
if not CSV_PATH.exists():
    print("\nWarning: conversion CSV not found at the resolved path.")
    # show CSVs in parent directory (if accessible)
    parent = CSV_PATH.parent
    print("Looking for CSV files in parent directory:", parent)
    try:
        candidates = sorted([p for p in parent.glob("*.csv")])
        if candidates:
            print("CSV files found in that directory:")
            for c in candidates:
                print(" -", c.name)
        else:
            print("No CSV files found in that directory.")
    except Exception as e:
        print("Could not list parent directory:", e)
    raise FileNotFoundError(f"Converted CSV not found: {CSV_PATH}\nPlease verify 'final_output_gust' in your config or place the conversion CSV at this path.")

# --- Haversine helper ---
def haversine_km(lon1, lat1, lon2, lat2):
    lon1, lat1, lon2, lat2 = map(radians, (lon1, lat1, lon2, lat2))
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = sin(dlat/2.0)**2 + cos(lat1) * cos(lat2) * sin(dlon/2.0)**2
    c = 2 * asin(sqrt(a))
    return 6371.0088 * c

# --- Main interactive lookup function (unchanged logic) ---
def prompt_and_lookup_converted(csv_path=CSV_PATH, tol_deg=1e-6, max_distance_km=None):
    """
    Prompt for lon/lat, find nearest converted point in csv_path, show map and return matched row dict.
    - tol_deg: small tolerance for exact match in degrees
    - max_distance_km: if set, will reject matches farther than this
    """
    if not os.path.isfile(csv_path):
        raise FileNotFoundError(f"Converted CSV not found: {csv_path}")

    # prompt user for coordinates
    try:
        lon = float(input("Enter Longitude: ").strip())
        lat = float(input("Enter Latitude:  ").strip())
    except Exception:
        raise ValueError("Invalid input. Enter numeric longitude and latitude (e.g. -81.35, 28.52).")

    display(Markdown(f"**🗺️ Query Location:** [{lat:.6f}, {lon:.6f}]"))

    df = pd.read_csv(csv_path)
    if not {'Lon','Lat'}.issubset(df.columns):
        raise ValueError("Converted CSV must contain 'Lon' and 'Lat' columns.")

    df_valid = df.dropna(subset=['Lon','Lat']).reset_index(drop=True)
    if df_valid.empty:
        raise ValueError("Converted CSV contains no valid Lon/Lat rows.")

    diffs_lon = np.abs(df_valid['Lon'].values - lon)
    diffs_lat = np.abs(df_valid['Lat'].values - lat)
    exact_mask = (diffs_lon <= tol_deg) & (diffs_lat <= tol_deg)

    if exact_mask.any():
        idx = int(np.flatnonzero(exact_mask)[0])
        matched = df_valid.iloc[idx].to_dict()
        match_type = 'exact'
        distance_km = haversine_km(lon, lat, matched['Lon'], matched['Lat'])
        print("Exact match found in conversion file.")
    else:
        pts = df_valid[['Lon','Lat']].values.astype(float)
        tree = cKDTree(pts)
        _, idx = tree.query([lon, lat], k=1)
        idx = int(idx)
        matched = df_valid.iloc[idx].to_dict()
        match_type = 'nearest'
        distance_km = haversine_km(lon, lat, matched['Lon'], matched['Lat'])
        print("No exact match; nearest converted point returned.")

    if (max_distance_km is not None) and (distance_km > max_distance_km):
        print(f"No converted point within {max_distance_km} km (nearest: {distance_km:.3f} km).")
        return {'match_type': 'none', 'distance_km': distance_km, 'nearest_lon': matched.get('Lon'), 'nearest_lat': matched.get('Lat')}

    print("\n--- Match Summary ---")
    print("Match type:", match_type)
    print(f"Distance to matched point: {distance_km:.3f} km")
    print("Matched Lon,Lat: {:.6f}, {:.6f}".format(matched['Lon'], matched['Lat']))
    for col in ['W_OT_3sg.', 'ActualT_3sg', 'z0_raster', 'dist_raster', 'CoastalFactor']:
        if col in matched:
            print(f"{col}: {matched[col]}")

    try:
        m = folium.Map(location=[lat, lon], zoom_start=12, tiles="CartoDB.Positron")
        folium.Marker([lat, lon],
                      popup=folium.Popup(f"Query: [{lat:.6f}, {lon:.6f}]<br>Distance to match: {distance_km:.3f} km", max_width=300),
                      icon=folium.Icon(color='red', icon='info-sign')).add_to(m)
        folium.Marker([matched['Lat'], matched['Lon']],
                      popup=folium.Popup(
                          "<b>Matched converted point</b><br>"
                          f"Lon: {matched['Lon']:.6f}<br>Lat: {matched['Lat']:.6f}<br>"
                          + "<br>".join([f"{c}: {matched[c]}" for c in ['ActualT_3sg','W_OT_3sg.','z0_raster','dist_raster'] if c in matched]),
                          max_width=400),
                      icon=folium.Icon(color='blue', icon='ok')).add_to(m)
        display(m)
    except Exception as e:
        print("Could not render folium map:", e)

    matched['match_type'] = match_type
    matched['distance_km'] = distance_km
    return matched

# Run interactive lookup (will prompt user for lon/lat)
result = prompt_and_lookup_converted()


Using conversion CSV path: /home/jupyter/MyProjects/PRJ-5778/Wind Speed Interpolation and Conversion/Interpolation&ConversionOutput/Wind speeds conversion.csv


Enter Longitude:  -85.2973
Enter Latitude:   29.80129


**🗺️ Query Location:** [29.801290, -85.297300]

No exact match; nearest converted point returned.

--- Match Summary ---
Match type: nearest
Distance to matched point: 0.100 km
Matched Lon,Lat: -85.297274, 29.802186
W_OT_3sg.: 124.4385405461592
ActualT_3sg: 112.37532244967078
z0_raster: 0.4073802778041126
dist_raster: 195.0
CoastalFactor: 0.9030588269233704
